- Ziel: wie kann ich einen städtischen Datensatz mit Crowdsourced Zusatzinfos anreichern (OSM + WikiData)
- Jupyter Notebook mit Geopandas + Folium Karte
- Daten
    - OGD/GeoServer: Kunst im Stadtraum (KiöR und KuB)
    - Zeigen: Overpass Query + OSM Wiki (Wie suche ich nach passendes Tags?), taginfo
    - Join mit OSM: `tourism=artwork`
    - Join mit WikiData zu einzelnen Kunstwerken, ihren Künstlern + Foto vom Künstler und Kunstwerk
- OSM
    - OSM Wiki zeigen
    - Overpass Turbo zeigen + Export als GeoJSON
- WikiData
    - Was ist es?
    - Kurze Erklärung zum Datenmodell
    - Wie kann ich Geodaten aus WikiData beziehen?
    - SPARQL-Abfrage für KioR (Bild + Text + Link auf Wikipedia
    - Weitergehende Infos hier: https://www.wikidata.org/wiki/Wikidata:Training
- Ganzer Datensatz zum KioR joinen und dann als GPKG exportieren und z.B. in QGIS öffnen
- Vor/Nachteile, für welche Datensätze eignet sich dieses Vorgehen?
- Quellen und weiterführende Infos zu WikiData + OSM

In [48]:
import os
import json
import requests
import folium
import geopandas
import pandas as pd
import utils

# Inhaltsverzeichnis

* [Daten aus OpenStreetMap laden](#Daten-aus-OpenStreetMap-laden)
    * [GeoJSON für Kunst im öffentlichen Raum (KiöR)](#GeoJSON-für-Kunst-im-öffentlichen-Raum-(KiöR))
    * [OSM-Daten laden](#OSM-Daten-laden)
    * [Karte mit den Resultaten](#Karte-mit-den-Resultaten)
    * [Spatial Join der zwei Quellen](#Spatial-Join-der-zwei-Quellen)
* [Daten aus WikiData laden](#Daten-aus-WikiData-laden)


# Daten aus OpenStreetMap laden
<sup>[⬆️ Inhaltverzeichnis](#Inhaltsverzeichnis)</sup>

Im ersten Teil schauen wir uns an, wie wir städtische Daten mit Daten aus OpenStreetMap (OSM) anreichern können.
Dazu laden wir uns zuerst den Datensatz «Kunst im öffentlichen Raum» via WFS und holen dann anschliessend weitere Daten zum Thema aus OSM.

## GeoJSON für Kunst im öffentlichen Raum (KiöR)
<sup>[⬆️ Inhaltverzeichnis](#Inhaltsverzeichnis)</sup>

[Via OGD-Portal](https://data.stadt-zuerich.ch/dataset?q=kunst+im+%C3%B6ffentlichen+raum) Datensatz [Kunst im Stadtraum](https://data.stadt-zuerich.ch/dataset/geo_kunst_im_stadtraum) von dort via GeoJSON auf das [Geoportal](https://www.stadt-zuerich.ch/geodaten/download/Kunst_im_Stadtraum?format=10009).

In [2]:
kioer_geojson_url = 'https://www.ogd.stadt-zuerich.ch/wfs/geoportal/Kunst_im_Stadtraum?service=WFS&version=1.1.0&request=GetFeature&outputFormat=GeoJSON&typename=view_kioer'
kioer_layer = 'view_kioer'
lv95 = 'EPSG:2056'
wgs84 = 'EPSG:4326'
wfs_url = 'https://www.ogd.stadt-zuerich.ch/wfs/geoportal/Kunst_im_Stadtraum' 
layers = utils.get_layers_from_wfs(wfs_url)
layers

{'view_kioer': {'srs': 'EPSG:2056'}, 'view_kub': {'srs': 'EPSG:2056'}}

In [3]:
r = requests.get(wfs_url, params={
    'service': 'WFS',
    'version': '1.0.0',
    'request': 'GetFeature',
    'typename': kioer_layer,
    'outputFormat': 'GeoJSON'
})
kioer_geo = r.json()
kioer_geo

{'type': 'FeatureCollection',
 'bbox': [8.474066, 47.327616, 8.605392, 47.425042],
 'features': [{'geometry': {'coordinates': [8.545688, 47.372467],
    'type': 'Point'},
   'id': 'view_kioer.84',
   'properties': {'autoren': 'Barbara Roth (*1950)\nThomas Ehrler (*1948)',
    'datierung': '1992',
    'id1': 84,
    'id_stadtplan': 1000084,
    'inventarnummer': '1396-01',
    'material': 'Bronze, Stein',
    'objectid': 84.0,
    'standort': 'Neumarkt, bei Neumarkt 4, AA4072',
    'titel': "L'étrangère"},
   'type': 'Feature'},
  {'geometry': None,
   'id': 'view_kioer.85',
   'properties': {'autoren': 'KünstlerIn nicht bekannt (nicht bekannt)\nAdolf Meyer (1867-1940)',
    'datierung': 'um 1550 (Figur um 1750, erneuert 1922)',
    'id1': 85,
    'id_stadtplan': 1000085,
    'inventarnummer': '1396-00',
    'material': 'Stein',
    'objectid': 85.0,
    'standort': None,
    'titel': '"Jupiterbrunnen"'},
   'type': 'Feature'},
  {'geometry': {'coordinates': [8.552012, 47.35384], 'type'

## OSM-Daten laden
<sup>[⬆️ Inhaltverzeichnis](#Inhaltsverzeichnis)</sup>

Daten von OpenStreetMap (OSM) können via Overpass API geladen werden.
Overpass hat eine eigene Abfragesprache ([Overpass QL](https://wiki.openstreetmap.org/wiki/Overpass_API/Overpass_QL)), mit der Objekte (Nodes, Ways, Relations) abgefragt werden können.

[Query in Overpass Turbo ausführen](https://osm.li/UfK)

In [4]:
artwork_zh = """
/*
Alle Kunstwerke (tourism=artwork) in der Stadt Zürich
*/
[out:json];
area["name"="Zürich"]["wikipedia"="de:Zürich"]->.perimeter; 
(
  nwr[tourism=artwork](area.perimeter);
);
out center;
"""
result = utils.overpass_query(artwork_zh)
result

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'properties': {'type': 'node',
    'id': 268472148,
    'tags': {'artist_name': 'Jean Tinguely',
     'name': 'Heureka',
     'tourism': 'artwork',
     'wheelchair': 'yes',
     'wikidata': 'Q1378316'}},
   'geometry': {'type': 'Point', 'coordinates': [8.552309, 47.3530162]}},
  {'type': 'Feature',
   'properties': {'type': 'node',
    'id': 356298160,
    'tags': {'artist': 'Richard Kissling',
     'artist:wikidata': 'Q120459',
     'artist_name': 'Richard Kissling',
     'artwork_type': 'sculpture',
     'info': 'Hat die Credit Suisse gegründet und mit dem Gewinn den Gotthardtunnel gebaut',
     'name': 'Alfred Escher-Statue',
     'name:etymology:wikidata': 'Q115569',
     'subject:wikidata': 'Q115569',
     'tourism': 'artwork',
     'wheelchair': 'yes',
     'wikidata': 'Q27229673',
     'wikipedia': 'de:Alfred Escher-Denkmal'}},
   'geometry': {'type': 'Point', 'coordinates': [8.5399549, 47.3771287]}},
  {'type':

## Karte mit den Resultaten
<sup>[⬆️ Inhaltverzeichnis](#Inhaltsverzeichnis)</sup>

In [5]:
# Basiskarte mit GeoJSON layer
m = folium.Map(location=[47.38, 8.53], zoom_start=13, tiles=None)
folium.raster_layers.WmsTileLayer(
    url='https://www.ogd.stadt-zuerich.ch/wms/geoportal/Basiskarte_Zuerich_Raster_Grau',
    layers='Basiskarte Zürich Raster Grau',
    name='Zürich - Basiskarte',
    fmt='image/png',
    overlay=False,
    control=False,
    autoZindex=False,
).add_to(m)

# KiöR-Daten hinzufügen
kioer_layer = folium.FeatureGroup(name='KiöR', show=True)
utils.style_layer(kioer_geo, kioer_layer, icon_color='#031cff', icon='certificate', prefix='fa')
kioer_layer.add_to(m)

# OSM-Daten hinzufügen
osm_layer = folium.FeatureGroup(name='OSM: tourism=artwork', show=True)
utils.style_layer(result, osm_layer, icon_color='#ff033e', icon='fire', prefix='fa')
osm_layer.add_to(m)

# Add controls for layers
folium.LayerControl().add_to(m)
m

## Spatial Join der zwei Quellen
<sup>[⬆️ Inhaltverzeichnis](#Inhaltsverzeichnis)</sup>

In [6]:
kioer_df = geopandas.GeoDataFrame.from_features(kioer_geo, crs=wgs84)
kioer_df

geometry  \
0    POINT (8.54569 47.37247)   
1                        None   
2    POINT (8.55201 47.35384)   
3    POINT (8.52583 47.37414)   
4    POINT (8.52136 47.37019)   
..                        ...   
401  POINT (8.53869 47.39200)   
402  POINT (8.54768 47.40317)   
403  POINT (8.52653 47.37720)   
404  POINT (8.54873 47.37053)   
405                      None   

                                               autoren  \
0          Barbara Roth (*1950)\nThomas Ehrler (*1948)   
1    KünstlerIn nicht bekannt (nicht bekannt)\nAdol...   
2                             Franz Wanger (1880-1945)   
3             KünstlerIn nicht bekannt (nicht bekannt)   
4                          Silvio Mattioli (1929-2011)   
..                                                 ...   
401                              L / B (*1972 / *1967)   
402  Emil Schäfer (1878-1958)\nArnold Huggler (1894...   
403                             Uli Schoop (1903-1990)   
404                        Baptist Hoerbst (1850-1927)   
405                                               None   

                                  datierung  id1  id_stadtplan inventarnummer  \
0                                      1992   84       1000084        1396-01   
1    um 1550 (Figur um 1750, erneuert 1922)   85       1000085        1396-00   
2                     1907 (platziert 1910)   86       1000086          58-00   
3                                  ca. 1916   87       1000087          85-00   
4                                 1984/1985   88       1000088         566-00   
..                                      ...  ...           ...            ...   
401                               2002-2003  402       1000402          48-00   
402          1937 (Brunnen), 1941 (Plastik)  403       1000403         863-00   
403                                ca. 1975  404       1000404         563-00   
404                                    1883  405       1000405          19-00   
405                                    2020  406       1000406         100023   

                                      material  objectid  \
0                                Bronze, Stein      84.0   
1                                        Stein      85.0   
2                                Kupfer, Stein      86.0   
3                                Bronze, Eisen      87.0   
4                             Chromnickelstahl      88.0   
..                                         ...       ...   
401                                      Beton     402.0   
402  Bronze (Plastik), Stein (Brunnen, Sockel)     403.0   
403           Bronze (Plastik), Beton (Sockel)     404.0   
404                                      Stein     405.0   
405                         Sound-Installation     406.0   

                                              standort                   titel  
0                     Neumarkt, bei Neumarkt 4, AA4072             L'étrangère  
1                                                 None        "Jupiterbrunnen"  
2         Zürichhorn, bei Bellerivestrasse 150, RI4672  Schweizerpsalm-Denkmal  
3    Vorplatz Bezirksgebäude, bei Badenerstrasse 90...            [Kandelaber]  
4    Bankgebäude UBS Zürich-Wiedikon, Vorplatz , be...          [Stahlplastik]  
..                                                 ...                     ...  
401  Schaffhauserplatz, bei Schaffhauserstrasse 57 ...             Der Brunnen  
402  Berninaplatz, bei Schaffhauserstrasse 248, OE3799   [Brunnen mit "Fuchs"]  
403  vor Kollerhof, Kreisgebäude 4, bei Hohlstrasse...                 [Fuchs]  
404                 Heimplatz, bei Heimplatz 6, AA4138      Ignaz-Heim-Denkmal  
405                                               None           Harmonic Gate  

[406 rows x 10 columns]

In [7]:
osm_df = geopandas.GeoDataFrame.from_features(result, crs=wgs84)
osm_df

geometry  type         id       artist_name  \
0    POINT (8.55231 47.35302)  node  268472148     Jean Tinguely   
1    POINT (8.53995 47.37713)  node  356298160  Richard Kissling   
2    POINT (8.54028 47.36588)  node  489786064               NaN   
3    POINT (8.54517 47.39695)  node  692155260               NaN   
4    POINT (8.53632 47.41425)  node  693205583               NaN   
..                        ...   ...        ...               ...   
242  POINT (8.53840 47.36974)   way  617727049               NaN   
243  POINT (8.55001 47.39691)   way  647033703               NaN   
244  POINT (8.54121 47.36601)   way  667718520  Hermann Hubacher   
245  POINT (8.54027 47.36589)   way  667718521               NaN   
246  POINT (8.54156 47.36706)   way  667718524               NaN   

                      name  tourism wheelchair   wikidata            artist  \
0                  Heureka  artwork        yes   Q1378316               NaN   
1     Alfred Escher-Statue  artwork        yes  Q27229673  Richard Kissling   
2    Blumenuhr Bürkliplatz  artwork        yes        NaN               NaN   
3           Schwester Mond  artwork    limited  Q55166775               NaN   
4                    Stier  artwork        NaN        NaN               NaN   
..                     ...      ...        ...        ...               ...   
242              Snow Moon  artwork        NaN        NaN               NaN   
243    Georg Büchner Platz  artwork        NaN        NaN               NaN   
244                Ganymed  artwork        yes  Q27229968               NaN   
245  Blumenuhr Bürkliplatz  artwork        yes        NaN               NaN   
246                    NaN  artwork        NaN        NaN               NaN   

    artist:wikidata  ... leisure playground backrest access mapillary area  \
0               NaN  ...     NaN        NaN      NaN    NaN       NaN  NaN   
1           Q120459  ...     NaN        NaN      NaN    NaN       NaN  NaN   
2               NaN  ...     NaN        NaN      NaN    NaN       NaN  NaN   
3               NaN  ...     NaN        NaN      NaN    NaN       NaN  NaN   
4               NaN  ...     NaN        NaN      NaN    NaN       NaN  NaN   
..              ...  ...     ...        ...      ...    ...       ...  ...   
242             NaN  ...     NaN        NaN      NaN    NaN       NaN  NaN   
243             NaN  ...     NaN        NaN      NaN    NaN       NaN  yes   
244         Q870322  ...     NaN        NaN      NaN    NaN       NaN  yes   
245             NaN  ...  garden        NaN      NaN    NaN       NaN  NaN   
246             NaN  ...     NaN        NaN      NaN    NaN       NaN  yes   

        highway  lit surface  year  
0           NaN  NaN     NaN   NaN  
1           NaN  NaN     NaN   NaN  
2           NaN  NaN     NaN   NaN  
3           NaN  NaN     NaN   NaN  
4           NaN  NaN     NaN   NaN  
..          ...  ...     ...   ...  
242         NaN  NaN     NaN   NaN  
243  pedestrian   no  tartan   NaN  
244         NaN  NaN     NaN  1952  
245         NaN  NaN     NaN   NaN  
246         NaN  NaN     NaN   NaN  

[247 rows x 57 columns]

In [41]:
# drop all elements with empty geometry
kior_buf = kioer_df.dropna(subset=['geometry']).reset_index(drop=True)
osm_buf = osm_df.dropna(subset=['geometry']).reset_index(drop=True)

# CRS zu LV95 re-projezieren
kior_buf = kior_buf.to_crs(lv95) # convert to plannar coordinate system
osm_buf = osm_buf.to_crs(lv95) # convert to plannar coordinate system

# Buffer um die Geometrien hinzufügen (10 Meter)
kior_buf['geometry'] = kior_buf.geometry.buffer(10) 
osm_buf['geometry'] = osm_buf.geometry.buffer(10)

In [42]:
# Basiskarte mit GeoJSON layer
bm = folium.Map(location=[47.38, 8.53], zoom_start=13, tiles=None)
folium.raster_layers.WmsTileLayer(
    url='https://www.ogd.stadt-zuerich.ch/wms/geoportal/Basiskarte_Zuerich_Raster_Grau',
    layers='Basiskarte Zürich Raster Grau',
    name='Zürich - Basiskarte',
    fmt='image/png',
    overlay=False,
    control=False,
    autoZindex=False,
).add_to(bm)
folium.features.GeoJson(
    kior_buf.to_crs(wgs84).to_json(),
    tooltip=folium.features.GeoJsonTooltip(
        fields=['titel', 'autoren', 'datierung', 'material'],
        aliases=['Titel:', 'Künstler:', 'Datierung:', 'Material:'],    
    )
).add_to(bm)

folium.features.GeoJson(
    osm_buf.to_crs(wgs84).to_json(),
    style_function=lambda x: {'fillColor': '#FF0000', 'color': '#FF0000'},
    tooltip=folium.features.GeoJsonTooltip(
        fields=['name', 'artist_name', 'wikidata'],
        aliases=['Titel:', 'Künstler:', "Wikidata:"],                      
    )
).add_to(bm)
bm

In [43]:
# spatial join über die beiden Geometrien
sjoin_kunst = geopandas.sjoin(kior_buf, osm_buf, how='left', predicate='intersects', lsuffix='kior', rsuffix='osm').reset_index()

# Wie zurück zu WGS84
sjoin_kunst = sjoin_kunst.to_crs(wgs84)


with pd.option_context('display.max_rows', None, 'display.max_columns', None):  # more options can be specified also
    display(sjoin_kunst[['titel', 'name', 'autoren', 'artist_name', 'material_kior', 'material_osm', 'datierung']])

titel  \
0                                          L'étrangère   
1                               Schweizerpsalm-Denkmal   
2                                         [Kandelaber]   
3                                       [Stahlplastik]   
4                                  "Murmeltierbrunnen"   
5                         [Wandbrunnen mit Broncekopf]   
6                           [Stehende weibliche Figur]   
7                                        [Fünf Poller]   
8                                              Muschel   
9                                              [Büste]   
10                    Kugellager oder runde Steine (I)   
11                    Kugellager oder runde Steine (I)   
12                               "Die fleissige Biene"   
13                            [Brunnentrog mit Wappen]   
14                            [Flötenspielender Knabe]   
15                                     "Orellibrunnen"   
16                                  Fünf Brunnen (III)   
17                      [Brunnen mit Eule (auf Stele)]   
18                       Grabmal Guido Otto Wesendonck   
19                             "Alfred-Escher-Brunnen"   
20                                             Heureka   
21                                          "Sitzende"   
22                                    "Pelikanbrunnen"   
23           [Wandgestaltung Unterführung Langstrasse]   
24                               [Brunnen mit "Taube"]   
25                                  "Findlingsbrunnen"   
26                                     [Brunnenschale]   
27                              [Steinvase auf Sockel]   
28                       [Zierbrunnen mit Floragöttin]   
29                                      Leutschenlicht   
30                   Kugellager oder runde Steine (II)   
31                                  "Feldmann-Brunnen"   
32                            [Wandbrunnen mit Relief]   
33                                    "Fischerbrunnen"   
34                       [Brunnen "Mädchen mit Vogel"]   
35                                             [Flora]   
36                 [Brunnen "Kniende weibliche Figur"]   
37                        [Brunnen mit drei Pinguinen]   
38   [Wandbrunnen "Kauernde" und versch. Steinreliefs]   
39                                  Denkmal der Arbeit   
40                                    [Wappen Seebach]   
41                      [Brunnen mit Plastik "Frosch"]   
42                               Aequatorial Sonnenuhr   
43                                    [Drei Flamingos]   
44                                      "Dianabrunnen"   
45                                   "Amazonenbrunnen"   
46                                    [Brunnenplastik]   
47                                           Zahlenzug   
48                             [Pergola mit Windspiel]   
49                                          Lichtblick   
50                                Richard-Wagner-Stele   
51                                         "Liegender"   
52                                          "Dschumbo"   
53                                     "Büeblibrunnen"   
54                          [Brunnen "Knabe mit Ball"]   
55                                        [Ohne Titel]   
56                                        [Ohne Titel]   
57                           [Brunnen mit Fischrelief]   
58                                       "Froschkönig"   
59                                          Funktionär   
60                          Heinrich-Zollinger-Denkmal   
61                                 "Basiliskenbrunnen"   
62   [Zwei Brunnen mit Sitzbänken und je einer Figu...   
63                                   [Männliche Figur]   
64                                       "Kapellenweg"   
65                                          "Die Zeit"   
66                                       "Zwei Frauen"   
67                                            Artisten   
68                     [Brunnen mit liegender G

In [44]:
folium.features.GeoJson(
    sjoin_kunst.to_json(),
    style_function=lambda x: {'fillColor': '#09bd63', 'color': '#09bd63'},
    tooltip=folium.features.GeoJsonTooltip(
        fields=['name', 'artist_name', 'wikidata'],
        aliases=['Titel:', 'Künstler:', "Wikidata:"],                      
    )
).add_to(bm)
bm

In [46]:
# OSM-Einträge ohne Match
osm_no_match = osm_df[(~osm_df.id.isin(sjoin_kunst.id))].reset_index()
osm_no_match

index                  geometry  type          id artist_name  \
0       2  POINT (8.54028 47.36588)  node   489786064         NaN   
1       3  POINT (8.54517 47.39695)  node   692155260         NaN   
2       4  POINT (8.53632 47.41425)  node   693205583         NaN   
3       5  POINT (8.57885 47.36310)  node   726662427   W. Martin   
4       6  POINT (8.55000 47.40736)  node   942821382         NaN   
..    ...                       ...   ...         ...         ...   
81    240  POINT (8.54495 47.39678)  node  8989236634         NaN   
82    241  POINT (8.54890 47.39786)  node  8989556719         NaN   
83    242  POINT (8.53840 47.36974)   way   617727049         NaN   
84    243  POINT (8.55001 47.39691)   way   647033703         NaN   
85    245  POINT (8.54027 47.36589)   way   667718521         NaN   

                     name  tourism wheelchair   wikidata artist  ... leisure  \
0   Blumenuhr Bürkliplatz  artwork        yes        NaN    NaN  ...     NaN   
1          Schwester Mond  artwork    limited  Q55166775    NaN  ...     NaN   
2                   Stier  artwork        NaN        NaN    NaN  ...     NaN   
3                 Elefant  artwork        NaN  Q27230070    NaN  ...     NaN   
4                     NaN  artwork        NaN        NaN    NaN  ...     NaN   
..                    ...      ...        ...        ...    ...  ...     ...   
81           Bruder Sonne  artwork        NaN        NaN    NaN  ...     NaN   
82                    NaN  artwork        NaN        NaN    NaN  ...     NaN   
83              Snow Moon  artwork        NaN        NaN    NaN  ...     NaN   
84    Georg Büchner Platz  artwork        NaN        NaN    NaN  ...     NaN   
85  Blumenuhr Bürkliplatz  artwork        yes        NaN    NaN  ...  garden   

   playground backrest access mapillary area     highway  lit surface year  
0         NaN      NaN    NaN       NaN  NaN         NaN  NaN     NaN  NaN  
1         NaN      NaN    NaN       NaN  NaN         NaN  NaN     NaN  NaN  
2         NaN      NaN    NaN       NaN  NaN         NaN  NaN     NaN  NaN  
3         NaN      NaN    NaN       NaN  NaN         NaN  NaN     NaN  NaN  
4         NaN      NaN    NaN       NaN  NaN         NaN  NaN     NaN  NaN  
..        ...      ...    ...       ...  ...         ...  ...     ...  ...  
81        NaN      NaN    NaN       NaN  NaN         NaN  NaN     NaN  NaN  
82        NaN      NaN    NaN       NaN  NaN         NaN  NaN     NaN  NaN  
83        NaN      NaN    NaN       NaN  NaN         NaN  NaN     NaN  NaN  
84        NaN      NaN    NaN       NaN  yes  pedestrian   no  tartan  NaN  
85        NaN      NaN    NaN       NaN  NaN         NaN  NaN     NaN  NaN  

[86 rows x 58 columns]

In [49]:
osm_no_match.to_file(os.path.join('..', 'kunst_package.gpkg'), layer='osm_no_match', driver="GPKG")
sjoin_kunst.to_file(os.path.join('..', 'kunst_package.gpkg'), layer='kioer_osm_match', driver="GPKG")

In [26]:
# Das GeoPackage lässt sich z.B. in QGIS öffnen

# Daten aus WikiData laden
<sup>[⬆️ Inhaltverzeichnis](#Inhaltsverzeichnis)</sup>

In [ ]:
# daten via WikiData-Verweise von OSM holen (z.B. Bild, weitere Infos zum Künstler)
# direkte SPARQL-Query auf WikiData